In [1]:
import os
import re
import time
import math
import torch
import random
import pickle
import os.path
import torchtext
import torchaudio
import matplotlib
import numpy as np
import scipy.signal
import pandas as pd
import torch.nn as nn
import librosa.display
import sentencepiece as spm
import IPython.display as ipd
import matplotlib.pyplot as plt
import torchaudio.transforms as T
import torchaudio.functional as AF




from tqdm import tqdm
from torch import Tensor
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from timeit import default_timer as timer
from torch.nn.utils.rnn import pad_sequence
from torchmetrics.functional import word_error_rate
from torchmetrics.functional import char_error_rate
from nltk.translate.bleu_score import sentence_bleu
from torch.utils.data.distributed import DistributedSampler
from torch.nn.parallel import DistributedDataParallel as DDP




In [2]:
train_csv = pd.read_csv('../text_data/combine_common_train.csv', index_col = None)


In [3]:
train_csv

voice  \
0       common_voice_fr_17299459.mp3   
1       common_voice_fr_17299553.mp3   
2       common_voice_fr_17299638.mp3   
3       common_voice_fr_17299707.mp3   
4       common_voice_fr_17299709.mp3   
...                              ...   
130592  common_voice_fr_20046205.mp3   
130593  common_voice_fr_20046206.mp3   
130594  common_voice_fr_20046217.mp3   
130595  common_voice_fr_20046218.mp3   
130596  common_voice_fr_20046240.mp3   

                                                     text  \
0                                            C’est clair.   
1       Voilà pourquoi, à titre personnel, je voterai ...   
2       La préparation a durée d'Août à Décembre, soit...   
3       Heureusement que Monsieur Carrez essaie de rat...   
4       Au niveau des outils d'analyse statique, vous ...   
...                                                   ...   
130592  James Burton y a noté une marque de maçon en c...   
130593       Dis mon pitchoun, tu es sûr que ça a marché?   
130594         Elle bénéficie d'un pouvoir réglementaire.   
130595  Les reproches envers le nationalisme chinois s...   
130596  En hiver, il est basé à Gênes en Italie pour p...   

                                                    text2  
0                                          that is clear.  
1       this is why on a personal note i will vote for...  
2       the preparation lasted from august to december...  
3       fortunately mr carrez is trying to rectify the...  
4       in terms of static analysis tools you can find...  
...                                                   ...  
130592  james burton noted a mason's mark there in red...  
130593                   hey baby are you sure it worked.  
130594                       it has regulatory authority.  
130595  criticisms of chinese nationalism are diverse ...  
130596  in winter it is in genoa italy in order to par...  

[130597 rows x 3 columns]

In [20]:
eval_csv = pd.read_csv('../text_data/combine_common_dev.csv', index_col = None)


In [21]:
eval_csv

voice  \
0      common_voice_fr_17300270.mp3   
1      common_voice_fr_17300274.mp3   
2      common_voice_fr_17300275.mp3   
3      common_voice_fr_17300276.mp3   
4      common_voice_fr_17301085.mp3   
...                             ...   
14754  common_voice_fr_20045646.mp3   
14755  common_voice_fr_20045660.mp3   
14756  common_voice_fr_20045662.mp3   
14757  common_voice_fr_20045681.mp3   
14758  common_voice_fr_20045682.mp3   

                                                    text  \
0      Elle va permettre de favoriser durablement une...   
1      Il faut réhabiliter l’impôt, la contribution à...   
2      Je retire l’amendement numéro cent cinquante-c...   
3      Or Jean-Patrick Gille vient de dire que l’atte...   
4               Je mets aux voix l’amendement numéro un.   
...                                                  ...   
14754  Il se trouve au sud de Dammastock et au nord d...   
14755  La société de Bourse poursuit ses activités ma...   
14756  Il signe également le second meilleur démarrag...   
14757                      Jozef retourne au Lokomotíva.   
14758        Il est diplômé de l'université du Maryland.   

                                                   text2  
0      it'll help spur the growth of that sector cont...  
1      it is necessary to rehabilitate the tax the co...  
2      i withdraw amendment number one hundred and fi...  
3      but jean patrick gille just said that the wait...  
4       i will now put to the vote amendment number one.  
...                                                  ...  
14754  it is located south of dammastock and north of...  
14755  the brokerage carries on its activities despit...  
14756  it also indicates the second best start to kea...  
14757                     jozef goes back to lokomotiva.  
14758             he graduated from maryland university.  

[14759 rows x 3 columns]

# ReSTART

In [22]:


device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

torch.cuda.manual_seed_all(777)

torch.cuda.set_device(0)




In [23]:

PRAAT_CHANGEGENDER_PITCHMEDIAN_DEFAULT = 0.0
PRAAT_CHANGEGENDER_FORMANTSHIFTRATIO_DEFAULT = 1.0
PRAAT_CHANGEGENDER_PITCHSHIFTRATIO_DEFAULT = 1.0
PRAAT_CHANGEGENDER_PITCHRANGERATIO_DEFAULT = 1.0
PRAAT_CHANGEGENDER_DURATIONFACTOR_DEFAULT = 1.0

def power_ratio(r: float, a: float, b: float):
    return a * math.pow((b / a), r)


# peq
def parametric_equalizer(wav: torch.Tensor, sr: int) -> torch.Tensor:
    cutoff_low_freq = 60.
    cutoff_high_freq = 10000.

    q_min = 2
    q_max = 5

    num_filters = 8 + 2  # 8 for peak, 2 for high/low
    key_freqs = [
        power_ratio(float(z) / (num_filters), cutoff_low_freq, cutoff_high_freq)
        for z in range(num_filters)
    ]
    Qs = [
        power_ratio(random.uniform(0, 1), q_min, q_max)
        for _ in range(num_filters)
    ]
    gains = [random.uniform(-12, 12) for _ in range(num_filters)]

    # peak filters
    for i in range(1, 9):
        wav = apply_iir_filter(
            wav,
            ftype='peak',
            dBgain=gains[i],
            cutoff_freq=key_freqs[i],
            sample_rate=sr,
            Q=Qs[i]
        )

    # high-shelving filter
    wav = apply_iir_filter(
        wav,
        ftype='high',
        dBgain=gains[-1],
        cutoff_freq=key_freqs[-1],
        sample_rate=sr,
        Q=Qs[-1]
    )

    # low-shelving filter
    wav = apply_iir_filter(
        wav,
        ftype='low',
        dBgain=gains[0],
        cutoff_freq=key_freqs[0],
        sample_rate=sr,
        Q=Qs[0]
    )

    return wav


# implemented using the cookbook https://webaudio.github.io/Audio-EQ-Cookbook/audio-eq-cookbook.html
def lowShelf_coeffs(dBgain, cutoff_freq, sample_rate, Q):
    A = math.pow(10, dBgain / 40.)

    w0 = 2 * math.pi * cutoff_freq / sample_rate
    alpha = math.sin(w0) / 2 / Q
    # alpha = alpha / math.sqrt(2) * math.sqrt(A + 1 / A)

    b0 = A * ((A + 1) - (A - 1) * math.cos(w0) + 2 * math.sqrt(A) * alpha)
    b1 = 2 * A * ((A - 1) - (A + 1) * math.cos(w0))
    b2 = A * ((A + 1) - (A - 1) * math.cos(w0) - 2 * math.sqrt(A) * alpha)

    a0 = (A + 1) + (A - 1) * math.cos(w0) + 2 * math.sqrt(A) * alpha
    a1 = -2 * ((A - 1) + (A + 1) * math.cos(w0))
    a2 = (A + 1) + (A - 1) * math.cos(w0) - 2 * math.sqrt(A) * alpha
    return b0, b1, b2, a0, a1, a2


def highShelf_coeffs(dBgain, cutoff_freq, sample_rate, Q):
    A = math.pow(10, dBgain / 40.)

    w0 = 2 * math.pi * cutoff_freq / sample_rate
    alpha = math.sin(w0) / 2 / Q
    # alpha = alpha / math.sqrt(2) * math.sqrt(A + 1 / A)

    b0 = A * ((A + 1) + (A - 1) * math.cos(w0) + 2 * math.sqrt(A) * alpha)
    b1 = -2 * A * ((A - 1) + (A + 1) * math.cos(w0))
    b2 = A * ((A + 1) + (A - 1) * math.cos(w0) - 2 * math.sqrt(A) * alpha)

    a0 = (A + 1) - (A - 1) * math.cos(w0) + 2 * math.sqrt(A) * alpha
    a1 = 2 * ((A - 1) - (A + 1) * math.cos(w0))
    a2 = (A + 1) - (A - 1) * math.cos(w0) - 2 * math.sqrt(A) * alpha
    return b0, b1, b2, a0, a1, a2


def peaking_coeffs(dBgain, cutoff_freq, sample_rate, Q):
    A = math.pow(10, dBgain / 40.)

    w0 = 2 * math.pi * cutoff_freq / sample_rate
    alpha = math.sin(w0) / 2 / Q
    # alpha = alpha / math.sqrt(2) * math.sqrt(A + 1 / A)

    b0 = 1 + alpha * A
    b1 = -2 * math.cos(w0)
    b2 = 1 - alpha * A

    a0 = 1 + alpha / A
    a1 = -2 * math.cos(w0)
    a2 = 1 - alpha / A
    return b0, b1, b2, a0, a1, a2


def apply_iir_filter(wav: torch.Tensor, ftype, dBgain, cutoff_freq, sample_rate, Q, torch_backend=True):
    if ftype == 'low':
        b0, b1, b2, a0, a1, a2 = lowShelf_coeffs(dBgain, cutoff_freq, sample_rate, Q)
    elif ftype == 'high':
        b0, b1, b2, a0, a1, a2 = highShelf_coeffs(dBgain, cutoff_freq, sample_rate, Q)
    elif ftype == 'peak':
        b0, b1, b2, a0, a1, a2 = peaking_coeffs(dBgain, cutoff_freq, sample_rate, Q)
    else:
        raise NotImplementedError
    if torch_backend:
        return_wav = AF.biquad(wav, b0, b1, b2, a0, a1, a2)
    else:
        # https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.lfilter_zi.html
        wav_numpy = wav.numpy()
        b = np.asarray([b0, b1, b2])
        a = np.asarray([a0, a1, a2])
        zi = scipy.signal.lfilter_zi(b, a) * wav_numpy[0]
        return_wav, _ = scipy.signal.lfilter(b, a, wav_numpy, zi=zi)
        return_wav = torch.from_numpy(return_wav)
    return return_wav


peq = parametric_equalizer

def g(wav: torch.Tensor, sr: int) -> torch.Tensor:
    wav = peq(wav, sr)
    return wav

In [24]:
from typing import Optional, Tuple

import torch


__all__ = ["Conformer"]


def _lengths_to_padding_mask(lengths: torch.Tensor) -> torch.Tensor:
    batch_size = lengths.shape[0]
    max_length = int(torch.max(lengths).item())
    padding_mask = torch.arange(max_length, device=lengths.device, dtype=lengths.dtype).expand(
        batch_size, max_length
    ) >= lengths.unsqueeze(1)
    return padding_mask


class _ConvolutionModule(torch.nn.Module):
    r"""Conformer convolution module.

    Args:
        input_dim (int): input dimension.
        num_channels (int): number of depthwise convolution layer input channels.
        depthwise_kernel_size (int): kernel size of depthwise convolution layer.
        dropout (float, optional): dropout probability. (Default: 0.0)
        bias (bool, optional): indicates whether to add bias term to each convolution layer. (Default: ``False``)
        use_group_norm (bool, optional): use GroupNorm rather than BatchNorm. (Default: ``False``)
    """

    def __init__(
        self,
        input_dim: int,
        num_channels: int,
        depthwise_kernel_size: int,
        dropout: float = 0.0,
        bias: bool = False,
        use_group_norm: bool = False,
    ) -> None:
        super().__init__()
        if (depthwise_kernel_size - 1) % 2 != 0:
            raise ValueError("depthwise_kernel_size must be odd to achieve 'SAME' padding.")
        self.layer_norm = torch.nn.LayerNorm(input_dim)
        self.sequential = torch.nn.Sequential(
            torch.nn.Conv1d(
                input_dim,
                2 * num_channels,
                1,
                stride=1,
                padding=0,
                bias=bias,
            ),
            torch.nn.GLU(dim=1),
            torch.nn.Conv1d(
                num_channels,
                num_channels,
                depthwise_kernel_size,
                stride=1,
                padding=(depthwise_kernel_size - 1) // 2,
                groups=num_channels,
                bias=bias,
            ),
            torch.nn.GroupNorm(num_groups=1, num_channels=num_channels)
            if use_group_norm
            else torch.nn.BatchNorm1d(num_channels),
            torch.nn.SiLU(),
            torch.nn.Conv1d(
                num_channels,
                input_dim,
                kernel_size=1,
                stride=1,
                padding=0,
                bias=bias,
            ),
            torch.nn.Dropout(dropout),
        )

    def forward(self, input: torch.Tensor) -> torch.Tensor:
        r"""
        Args:
            input (torch.Tensor): with shape `(B, T, D)`.

        Returns:
            torch.Tensor: output, with shape `(B, T, D)`.
        """
        x = self.layer_norm(input)
        x = x.transpose(1, 2)
        x = self.sequential(x)
        return x.transpose(1, 2)


class _FeedForwardModule(torch.nn.Module):
    r"""Positionwise feed forward layer.

    Args:
        input_dim (int): input dimension.
        hidden_dim (int): hidden dimension.
        dropout (float, optional): dropout probability. (Default: 0.0)
    """

    def __init__(self, input_dim: int, hidden_dim: int, dropout: float = 0.0) -> None:
        super().__init__()
        self.sequential = torch.nn.Sequential(
            torch.nn.LayerNorm(input_dim),
            torch.nn.Linear(input_dim, hidden_dim, bias=True),
            torch.nn.SiLU(),
            torch.nn.Dropout(dropout),
            torch.nn.Linear(hidden_dim, input_dim, bias=True),
            torch.nn.Dropout(dropout),
        )

    def forward(self, input: torch.Tensor) -> torch.Tensor:
        r"""
        Args:
            input (torch.Tensor): with shape `(*, D)`.

        Returns:
            torch.Tensor: output, with shape `(*, D)`.
        """
        return self.sequential(input)


class ConformerLayer(torch.nn.Module):
    r"""Conformer layer that constitutes Conformer.

    Args:
        input_dim (int): input dimension.
        ffn_dim (int): hidden layer dimension of feedforward network.
        num_attention_heads (int): number of attention heads.
        depthwise_conv_kernel_size (int): kernel size of depthwise convolution layer.
        dropout (float, optional): dropout probability. (Default: 0.0)
        use_group_norm (bool, optional): use ``GroupNorm`` rather than ``BatchNorm1d``
            in the convolution module. (Default: ``False``)
        convolution_first (bool, optional): apply the convolution module ahead of
            the attention module. (Default: ``False``)
    """

    def __init__(
        self,
        input_dim: int,
        ffn_dim: int,
        num_attention_heads: int,
        depthwise_conv_kernel_size: int,
        dropout: float = 0.0,
        use_group_norm: bool = False,
        convolution_first: bool = False,
    ) -> None:
        super().__init__()

        self.ffn1 = _FeedForwardModule(input_dim, ffn_dim, dropout=dropout)

        self.self_attn_layer_norm = torch.nn.LayerNorm(input_dim)
        self.self_attn = torch.nn.MultiheadAttention(input_dim, num_attention_heads, dropout=dropout)
        self.self_attn_dropout = torch.nn.Dropout(dropout)

        self.conv_module = _ConvolutionModule(
            input_dim=input_dim,
            num_channels=input_dim,
            depthwise_kernel_size=depthwise_conv_kernel_size,
            dropout=dropout,
            bias=True,
            use_group_norm=use_group_norm,
        )

        self.ffn2 = _FeedForwardModule(input_dim, ffn_dim, dropout=dropout)
        self.final_layer_norm = torch.nn.LayerNorm(input_dim)
        self.convolution_first = convolution_first

    def _apply_convolution(self, input: torch.Tensor) -> torch.Tensor:
        residual = input
        input = input.transpose(0, 1)
        input = self.conv_module(input)
        input = input.transpose(0, 1)
        input = residual + input
        return input

    def forward(self, input: torch.Tensor, key_padding_mask: Optional[torch.Tensor]) -> torch.Tensor:
        r"""
        Args:
            input (torch.Tensor): input, with shape `(T, B, D)`.
            key_padding_mask (torch.Tensor or None): key padding mask to use in self attention layer.

        Returns:
            torch.Tensor: output, with shape `(T, B, D)`.
        """
        residual = input
        x = self.ffn1(input)
        x = x * 0.5 + residual

        if self.convolution_first:
            x = self._apply_convolution(x)

        residual = x
        x = self.self_attn_layer_norm(x)
        x, _ = self.self_attn(
            query=x,
            key=x,
            value=x,
            key_padding_mask=key_padding_mask,
            need_weights=False,
        )
        x = self.self_attn_dropout(x)
        x = x + residual

        if not self.convolution_first:
            x = self._apply_convolution(x)

        residual = x
        x = self.ffn2(x)
        x = x * 0.5 + residual

        x = self.final_layer_norm(x)
        return x


class Conformer(torch.nn.Module):
    r"""Conformer architecture introduced in
    *Conformer: Convolution-augmented Transformer for Speech Recognition*
    :cite:`gulati2020conformer`.

    Args:
        input_dim (int): input dimension.
        num_heads (int): number of attention heads in each Conformer layer.
        ffn_dim (int): hidden layer dimension of feedforward networks.
        num_layers (int): number of Conformer layers to instantiate.
        depthwise_conv_kernel_size (int): kernel size of each Conformer layer's depthwise convolution layer.
        dropout (float, optional): dropout probability. (Default: 0.0)
        use_group_norm (bool, optional): use ``GroupNorm`` rather than ``BatchNorm1d``
            in the convolution module. (Default: ``False``)
        convolution_first (bool, optional): apply the convolution module ahead of
            the attention module. (Default: ``False``)

    Examples:
        >>> conformer = Conformer(
        >>>     input_dim=80,
        >>>     num_heads=4,
        >>>     ffn_dim=128,
        >>>     num_layers=4,
        >>>     depthwise_conv_kernel_size=31,
        >>> )
        >>> lengths = torch.randint(1, 400, (10,))  # (batch,)
        >>> input = torch.rand(10, int(lengths.max()), input_dim)  # (batch, num_frames, input_dim)
        >>> output = conformer(input, lengths)
    """

    def __init__(
        self,
        input_dim: int,
        num_heads: int,
        ffn_dim: int,
        num_layers: int,
        depthwise_conv_kernel_size: int,
        dropout: float = 0.0,
        use_group_norm: bool = False,
        convolution_first: bool = False,
    ):
        super().__init__()

        self.conformer_layers = torch.nn.ModuleList(
            [
                ConformerLayer(
                    input_dim,
                    ffn_dim,
                    num_heads,
                    depthwise_conv_kernel_size,
                    dropout=dropout,
                    use_group_norm=use_group_norm,
                    convolution_first=convolution_first,
                )
                for _ in range(num_layers)
            ]
        )

    def forward(self, input: torch.Tensor, lengths: torch.Tensor) -> Tuple[torch.Tensor, torch.Tensor]:
        r"""
        Args:
            input (torch.Tensor): with shape `(B, T, input_dim)`.
            lengths (torch.Tensor): with shape `(B,)` and i-th element representing
                number of valid frames for i-th batch element in ``input``.

        Returns:
            (torch.Tensor, torch.Tensor)
                torch.Tensor
                    output frames, with shape `(B, T, input_dim)`
                torch.Tensor
                    output lengths, with shape `(B,)` and i-th element representing
                    number of valid frames for i-th batch element in output frames.
        """
        encoder_padding_mask = _lengths_to_padding_mask(lengths)

        x = input.transpose(0, 1)
        for layer in self.conformer_layers:
            x = layer(x, encoder_padding_mask)
        return x.transpose(0, 1), lengths, encoder_padding_mask 

In [25]:
example_data = [[] for i in range(len(train_csv))] 

for i in range(len(train_csv)):
    example_data[i].append(train_csv['voice'][i])
    example_data[i].append(re.sub("[\,\…\~]", "", train_csv['text'][i]).lower())
    example_data[i].append(train_csv['text2'][i])

eval_data = [[] for i in range(len(eval_csv))] 

for i in range(len(eval_csv)):
    eval_data[i].append(eval_csv['voice'][i])
    eval_data[i].append(re.sub("[\,\…\~]", "", eval_csv['text'][i]).lower())
    eval_data[i].append(eval_csv['text2'][i])

In [26]:
kr_vocab_file = "../word_dict/fr_sp.model" ## Tokenizer
kr_vocab = spm.SentencePieceProcessor()
kr_vocab.load(kr_vocab_file)

en_vocab_file = "../word_dict/en_sp.model" 
en_vocab = spm.SentencePieceProcessor()
en_vocab.load(en_vocab_file)

def kr_tokenizer(sentence: str):

    return kr_vocab.encode_as_ids(sentence)

def en_tokenizer(sentence: str):

    return en_vocab.encode_as_ids(sentence)


In [27]:

class PositionalEncoding(nn.Module):
    def __init__(self, emb_size, max_len, dropout ):
        super(PositionalEncoding, self).__init__()
        
        den = torch.exp(- torch.arange(0, emb_size, 2) * math.log(10000) / emb_size) ## shape = (1,256)
        pos = torch.arange(0, max_len).reshape(max_len, 1) ## shape (maxlen, 1)
        
        pos_embedding = torch.zeros((max_len, emb_size))
        pos_embedding[:, 0::2] = torch.sin(pos * den)
        pos_embedding[:, 1::2] = torch.cos(pos * den)
        pos_embedding = pos_embedding.unsqueeze(0) ## batch, seq dim
        
        self.dropout = nn.Dropout(dropout)
        self.register_buffer('pos_embedding', pos_embedding) ## opimizer가 업데이트 하지 않음, 그러나 값은 존재, GPU연산 가능, 업데이트 하고싶지 않은 층
        
    def forward(self, token_embedding):

        return self.dropout(token_embedding + self.pos_embedding[:, :token_embedding.size(1), :]) ## batch length, dim
    
    
class Speech_PositionalEncoding(nn.Module):
    def __init__(self, emb_size, max_len, dropout ):
        super(Speech_PositionalEncoding, self).__init__()
        
        den = torch.exp(- torch.arange(0, emb_size, 2) * math.log(10000) / emb_size) ## shape = (1,256)
        pos = torch.arange(0, max_len).reshape(max_len, 1) ## shape (maxlen, 1)
        
        pos_embedding = torch.zeros((max_len, emb_size))
        pos_embedding[:, 0::2] = torch.sin(pos * den)
        pos_embedding[:, 1::2] = torch.cos(pos * den)
        pos_embedding = pos_embedding.unsqueeze(0) ## batch seq, dim
        
        self.dropout = nn.Dropout(dropout)
        self.register_buffer('pos_embedding', pos_embedding) ## opimizer가 업데이트 하지 않음, 그러나 값은 존재, GPU연산 가능, 업데이트 하고싶지 않은 층
        
    def forward(self, token_embedding):
   
        return self.dropout(token_embedding + self.pos_embedding[:, :token_embedding.size(1), :]) ## batch, length, dim
    

class TokenEmbedding(nn.Module):
    def __init__(self, vocab_size, emb_size):
        super(TokenEmbedding,self).__init__()
        self.embedding = nn.Embedding(vocab_size, emb_size, padding_idx = 0) ## 단어사전 
        self.emb_size = emb_size
    
    def forward(self, tokens):
        return self.embedding(tokens.long()) * math.sqrt(self.emb_size)

In [28]:
class Seq2SeqTransformer(nn.Module):
    def __init__(self, 
                 num_encoder_layers: int,
                 num_decoder_layers: int,
                 n_mel,
                 emb_size,
                 nhead,
                 src_vocab_size,
                 tgt_vocab_size,
                 max_len,
                 dim_feedforward = 512, 
                 dropout = 0.2):
        
        super(Seq2SeqTransformer,self).__init__()
        
#         self.transformer = Transformer(d_model = emb_size,
#                                       nhead = nhead,
#                                       num_encoder_layers = num_encoder_layers,
#                                       num_decoder_layers = num_decoder_layers,
#                                       dim_feedforward = dim_feedforward, dropout = dropout)
        
        self.conformer = Conformer(input_dim = emb_size,
                                   num_heads=nhead,
                                   ffn_dim = dim_feedforward,
                                   num_layers = num_encoder_layers,
                                   depthwise_conv_kernel_size = 31, 
                                   dropout = dropout)
        
        
        self.conformer_MT = Conformer(input_dim = emb_size,
                           num_heads=nhead,
                           ffn_dim = dim_feedforward,
                           num_layers = num_encoder_layers,
                           depthwise_conv_kernel_size = 31, 
                           dropout = dropout)
        
        
        self.decoder_layer = nn.TransformerDecoderLayer(d_model = emb_size,
                                                        dim_feedforward = dim_feedforward,
                                                        dropout= dropout,
                                                        nhead = nhead,
                                                        device = device, batch_first = True)
        
        self.transformer_decoder = nn.TransformerDecoder(self.decoder_layer, num_layers=num_decoder_layers)
        self.transformer_decoder_MT = nn.TransformerDecoder(self.decoder_layer, num_layers=num_decoder_layers)
        
        
        self.multihead_mapping = nn.MultiheadAttention(embed_dim = emb_size, num_heads = 4, batch_first = True, dropout = 0.4)
        
        self.after_multihead_ffn = _FeedForwardModule(emb_size, dim_feedforward, dropout=dropout)
        
        self.first_layer_norm = torch.nn.LayerNorm(emb_size)
        self.final_layer_norm = torch.nn.LayerNorm(emb_size)
        
        
        self.src_generator = nn.Linear(emb_size, src_vocab_size)
        self.tgt_generator = nn.Linear(emb_size, tgt_vocab_size)
        

        self.src_tok_emb = TokenEmbedding(src_vocab_size, emb_size) 
        self.tgt_tok_emb = TokenEmbedding(tgt_vocab_size, emb_size)

            
        self.positional_encoding = PositionalEncoding(emb_size, max_len, dropout = dropout)
    
        
        self.first_feature = int(emb_size/8)
        self.second_feature = int(emb_size/4)
        
        self.subsampling_conv = nn.Sequential(
                    nn.Conv2d(1, self.first_feature, kernel_size = (3,3), stride=1, padding=1),
                    nn.ReLU(),
                    nn.Conv2d(self.first_feature, self.first_feature, kernel_size= (3,3), stride=1, padding=1),
                    nn.ReLU(),
                    nn.MaxPool2d((2,2), stride=2),
                    nn.Conv2d(self.first_feature, self.second_feature, kernel_size= (3,3), stride=1, padding=1),
                    nn.ReLU(),
                    nn.Conv2d(self.second_feature, self.second_feature, kernel_size= (3,3), stride=1, padding=1),
                    nn.ReLU(),
                    nn.MaxPool2d((2,2), stride=2)
                )        
    
        self.sub_sampling_dim = n_mel>>2
        
        self.sub_sampling_fc = nn.Linear(in_features = self.sub_sampling_dim * self.second_feature, out_features = emb_size)

        self.dropout = nn.Dropout(dropout)
        
    def forward(self, src_speech, src_text, src_text_mask, src_text_padding_mask, tgt_text, tgt_text_mask, tgt_text_padding_mask,lengths):
        '''
         src : speeeh >> batch, legnth, dim
         tgt : text, if batch fisrt = [batch, seq_length] else [seq, batch]
        '''
        
        src_speech = src_speech.unsqueeze(1) ## batch, 1, length, dim
        src_speech = self.subsampling_conv(src_speech) #batch, output_channel, length, dim
        
        B, C, T, F = src_speech.size() 
        
        src_speech = src_speech.permute(0,2,1,3).contiguous().view(B, T, C*F) ## batch, channel, length, dim -> (batch, length, channel, dim) -> batch, length, (channel * dim)        
        src_speech = self.sub_sampling_fc(src_speech)
                
        src_speech_emb = self.positional_encoding(src_speech)    ## batch, seq, dim
        src_text_emb = self.positional_encoding(self.src_tok_emb(src_text))
        tgt_text_emb = self.positional_encoding(self.tgt_tok_emb(tgt_text))
        
        lengths = torch.tensor(list(map(int, (lengths / 4)))).to(device)
        
        memory = self.conformer(src_speech_emb, lengths) ## ASR 용 Conformer,  shape:batch, seq, dim 
        
        ASR_encoder_padding_mask = memory[2]
        ASR_memory = memory[0] ## batch,seq,dim 
        
        ASR_ctc_memory = self.src_generator(ASR_memory) ## CTC용 loss 계산용 Conformer vector
        MT_ctc_memory = self.tgt_generator(ASR_memory)
        
        
        
        ASR_outs = self.transformer_decoder(src_text_emb, ASR_memory, tgt_mask = src_text_mask, 
                                        tgt_key_padding_mask = src_text_padding_mask, 
                                        memory_key_padding_mask = ASR_encoder_padding_mask)
                
        MT_outs = self.transformer_decoder_MT(tgt_text_emb, ASR_memory, tgt_mask = tgt_text_mask,  
                                             tgt_key_padding_mask= tgt_text_padding_mask,
                                              memory_key_padding_mask= ASR_encoder_padding_mask) ### Conformer outs to Decoder
        
        
#         MT_memory = self.conformer_MT(temp_ASR_memory, lengths) ## MT 용 Conformer, Shape : batch, seq, dim
#         MT_encoder_padding_mask = MT_memory[2] ## memory_key_padding_mask
#         MT_memory = MT_memory[0]
        

        
#         residual = MT_outs
        
#         #MT_outs = self.first_layer_norm(MT_outs)
        
#         MT_outs, _ = self.multihead_mapping(MT_outs, temp_ASR_outs, temp_ASR_outs, src_text_padding_mask)
        
#         MT_outs = residual + MT_outs
        
#         MT_outs = self.dropout(MT_outs)
        
#         residual2 = MT_outs
        
#         MT_outs = self.after_multihead_ffn(MT_outs)
        
#         MT_outs = residual2 + MT_outs
        
#         MT_outs = self.final_layer_norm(MT_outs)
        
        return self.src_generator(ASR_outs), ASR_ctc_memory, self.tgt_generator(MT_outs), MT_ctc_memory
        
    
    
    
    def encode(self, src_speech, lengths):
        
        src_speech = src_speech.unsqueeze(1)
                
        src_speech = self.subsampling_conv(src_speech)
        
        B, C, T, F = src_speech.size()
        
        src_speech = src_speech.permute(0,2,1,3).contiguous().view(B, T, C*F)
                
        src_speech = self.sub_sampling_fc(src_speech)
                
        src_speech_emb = self.positional_encoding(src_speech)   ## Shape : batch, length, dim
        
        ASR_memory = self.conformer(src_speech_emb, lengths)
        
        return ASR_memory
    
    
    
    def decoder(self, src_text, ASR_memory, src_text_mask, ASR_memory_key_padding_mask, tgt_text, tgt_text_mask):
        
        ASR_outs = self.transformer_decoder(self.positional_encoding(self.src_tok_emb(src_text)),
                                       ASR_memory, tgt_mask = src_text_mask, memory_key_padding_mask= ASR_memory_key_padding_mask)
        
    
        MT_outs = self.transformer_decoder_MT(self.positional_encoding(self.tgt_tok_emb(tgt_text)),
                                       ASR_memory, tgt_mask = tgt_text_mask, memory_key_padding_mask = ASR_memory_key_padding_mask)
        
#         residual = MT_outs
        
#         #MT_outs = self.first_layer_norm(MT_outs)
        
#         MT_outs, _ = self.multihead_mapping(MT_outs, ASR_outs, ASR_outs)
        
#         MT_outs = residual + MT_outs
                
#         residual2 = MT_outs
        
#         MT_outs = self.after_multihead_ffn(MT_outs)
        
#         MT_outs = residual2 + MT_outs
        
#         MT_outs = self.final_layer_norm(MT_outs)
        
                
        return ASR_outs, MT_outs

In [29]:
def generate_square_subsequent_mask(sz):
    mask = (torch.triu(torch.ones((sz,sz)))== 1).T  ## 삼각행렬로 만든 뒤
    mask = mask.float().masked_fill(mask==0, float('-inf')).masked_fill(mask == 1, float(0.0)) ## 0은 -inf 와 같은 작은 값을 줘서 
    return mask

def create_mask(tgt):
    '''
    tgt = text, if batch_first = [batch, sequence], else [seq, batch]
    '''
    tgt_seq_len = tgt.shape[1]  ## sequence_length
    
    tgt_mask = generate_square_subsequent_mask(tgt_seq_len) ## 디코더에서 셀프 어텐션 할때 그 뒤를 못보게 마스킹
    
    tgt_padding_mask = (tgt == 0)
    return tgt_mask, tgt_padding_mask ## unsqueeze(0) 해줘서 배치 생성

In [30]:
max_length = 5000

In [31]:
SRC_VOCAB_SIZE = kr_vocab.GetPieceSize() 
TGT_VOCAB_SIZE = en_vocab.GetPieceSize() 
EMB_SIZE = 256
NHEAD = 4
FFN_HID_DIM = 512
BATCH_SIZE = 32
NUM_ENCODER_LAYERS = 10
NUM_DECODER_LAYERS = 4 ## 3 
N_MEL = 80

In [32]:
sr = 22050
n_fft = 512
win_length = n_fft
hop_length = 256

In [61]:
import os
import torch.utils.data
from librosa.util import normalize
from scipy.io.wavfile import read
from librosa.filters import mel as librosa_mel_fn

import pickle
import soundfile as sf
from scipy import signal
from scipy.signal import get_window
from librosa.filters import mel

MAX_WAV_VALUE = 32768.0

import os
import torch.utils.data
from librosa.util import normalize
from scipy.io.wavfile import read
from librosa.filters import mel as librosa_mel_fn

import pickle
import soundfile as sf
from scipy import signal
from scipy.signal import get_window
from librosa.filters import mel


def dynamic_range_compression(x, C=1, clip_val=1e-5):
    return np.log(np.clip(x, a_min=clip_val, a_max=None) * C)


def dynamic_range_decompression(x, C=1):
    return np.exp(x) / C


def dynamic_range_compression_torch(x, C=1, clip_val=1e-5):
    return torch.log(torch.clamp(x, min=clip_val) * C)
    # return torch.clamp(x, min=clip_val) * C


def dynamic_range_decompression_torch(x, C=1):
    return torch.exp(x) / C


def spectral_normalize_torch(magnitudes):
    output = dynamic_range_compression_torch(magnitudes)
    return output


def spectral_de_normalize_torch(magnitudes):
    output = dynamic_range_decompression_torch(magnitudes)
    return output


mel_basis = {}
hann_window = {}

def mel_spectrogram(y, n_fft=n_fft, num_mels=80, sampling_rate= sr, hop_size=hop_length, win_size=win_length, fmin=125, fmax=7600, center=False):
    global mel_basis, hann_window
    if fmax not in mel_basis:
        mel = librosa_mel_fn(sr=sampling_rate, n_fft=n_fft, n_mels=num_mels, fmin=fmin, fmax=fmax)
        mel_basis[str(fmax) + '_' + str(y.device)] = torch.from_numpy(mel).float().to(y.device)
        hann_window[str(y.device)] = torch.hann_window(win_size).to(y.device)
    
    # print(y.shape) # 45237, 1 (1024-256)/2, (1024-256)/2
    y = torch.nn.functional.pad(y.unsqueeze(0), (int((n_fft - hop_size) / 2), int((n_fft - hop_size) / 2)),
                                mode='reflect')
    y = y.squeeze(1)
    
    spec = torch.stft(y, n_fft, hop_length=hop_size, win_length=win_size, window=hann_window[str(y.device)],
                      center=center, pad_mode='reflect', normalized=False, onesided=True, return_complex = False) # return_complex =False

    spec = torch.sqrt(spec.pow(2).sum(-1) + (1e-9)) #???

    spec = torch.matmul(mel_basis[str(fmax) + '_' + str(y.device)], spec)
    spec = spectral_normalize_torch(spec)

    return spec


In [35]:
class AdamWarmup:
    
    def __init__(
            self,
            parameters,
            betas: Tuple[float, float],
            eps: float,
            weight_decay: float,
            warmup_staps: int,
            model_dim: int,
            scaler: float,
            step_size: int,
            *args,
            **kwargs
            ):
        self.optimizer = torch.optim.Adam(
            parameters,
            betas=betas,
            eps=eps,
            weight_decay=weight_decay
        )
        self.warmup_staps = warmup_staps
        self.model_dim = model_dim
        self.scaler = scaler
        self.peak = self.scaler / math.sqrt(self.model_dim)
        self.inv_warmup_staps = 1 / math.sqrt(self.warmup_staps ** 3)
        self.step_size = step_size
        self.counter = 0

    def get_lr(self, step: int) -> float:
        return self.peak * min(
            1 / math.sqrt(step),
            step * self.inv_warmup_staps
        )

    def step(self) -> None:
        self.counter += self.step_size
        lr = self.get_lr(self.counter)
        for param_group in self.optimizer.param_groups:
            param_group['lr'] = lr
        self.optimizer.step()

    def zero_grad(self):
        self.optimizer.zero_grad()

    def state_dict(self):
        return self.optimizer.state_dict()


In [62]:
transformer = Seq2SeqTransformer(NUM_ENCODER_LAYERS, NUM_DECODER_LAYERS, N_MEL, EMB_SIZE, NHEAD, SRC_VOCAB_SIZE, 
                                 TGT_VOCAB_SIZE, max_length, FFN_HID_DIM)

for p in transformer.parameters():
    if p.dim() > 1:
        nn.init.xavier_uniform_(p)

#transformer = transformer.to(device)

##loss_fn = nn.CTCLoss(blank = 0) ## torch.nn.CrossEntropyLoss(ignore_index = 0)

loss_fn = torch.nn.CrossEntropyLoss(ignore_index = 0, label_smoothing = 0.1)
loss_fn2 = torch.nn.CTCLoss(blank = 0, zero_infinity = True)

loss_MT_fn = torch.nn.CrossEntropyLoss(ignore_index = 0)


#optimizer = AdamWarmup(transformer.parameters(), betas = (0.9,0.98), eps = 1e-9, weight_decay=1e-6, warmup_staps = 2000, scaler = 0.05, model_dim = EMB_SIZE,  step_size = 1 ) 


optimizer = torch.optim.Adam(transformer.parameters(), lr =3e-4, betas = (0.9,0.98), eps = 1e-9, weight_decay=1e-6) #, weight_decay=1e-6
#scheduler = torch.optim.lr_scheduler.StepLR(optimizer, 50, gamma=0.5)
## lr = 4e-4 weight_decay = 1e-6 


In [63]:
transformer = transformer.to(device)
#transformer = DDP(transformer)

In [64]:
def sequential_transforms(*transforms):
    def func(txt_input):
        for transform in transforms:
            txt_input = transform(txt_input)
        return txt_input
    return func

def tensor_transform(token_ids):
    return torch.cat((torch.tensor([2]),
                     torch.tensor(token_ids),
                     torch.tensor([3])))
text_transform = {}


text_transform['kr'] = sequential_transforms(kr_tokenizer, tensor_transform) ## <tokenizing indexing 과 special token 추가> 식으로 진행
text_transform['en'] = sequential_transforms(en_tokenizer, tensor_transform)
## text_transform['kor'] = sequential_transforms(tokenizer, pre_vocab, tensor_transform)


In [65]:
def wav_aug(wav):
    
    padding_case = torch.randint(1, 4, (1,)).item()

    if padding_case ==1:
        padding_size = torch.randint(10, 3000, (1,)).item()
        wav = nn.functional.pad(wav[:, padding_size:], (0, padding_size))        
    
    elif padding_case == 2:
        padding_size = torch.randint(10, 3000, (1,)).item()
        wav = nn.functional.pad(wav[:, :-padding_size], (padding_size, 0))
    
    elif padding_case == 3:
        padding_size = torch.randint(10, 22050, (1,)).item()
        wav = nn.functional.pad(wav, (padding_size, padding_size))
    
    else:
        wav = wav

    return wav  

In [66]:

## aug 적용

class audio_dataset(Dataset): ## 오디오 파일로 로드
    
    def __init__(self, data_list: list, data_split: str = 'train'):
        
        self.max_len = len(data_list)
        self.data_list = data_list
        self.data_split = data_split
        
        self.time_masking = T.TimeMasking(time_mask_param = 50, p= 0.10)
        self.freq_masking = T.FrequencyMasking(freq_mask_param = 30)
        self.n_time_aug_blocks = 5
        
    def __len__(self):
        return self.max_len
    
    def __getitem__(self, idx):
        raw_audio = torchaudio.load('../voice_data/'+ self.data_split + '/' + self.data_list[idx][0]) ## output = 음원, (sampling, rate)
        resample_audio = torchaudio.functional.resample(raw_audio[0], orig_freq=48000, new_freq=22050) ## sampling
        
        if self.data_split == 'train':
            resample_audio = wav_aug(resample_audio)
            resample_audio = g(resample_audio, 22050)
            audio_mel = mel_spectrogram(resample_audio)
            for _ in range(self.n_time_aug_blocks):
                audio_mel = self.time_masking(audio_mel)
            audio_mel = self.freq_masking(audio_mel)
        else:
            audio_mel = mel_spectrogram(resample_audio)
        
        audio_mel = audio_mel.squeeze().permute(1,0) ## length, 80
        
        src_text = self.data_list[idx][1]
        
        tgt_text = self.data_list[idx][2]
        
        return audio_mel, src_text, tgt_text
    
    


In [67]:
def collate_fn(batch):
    
    src_speech, src_text, tgt_text, src_text_length, tgt_text_length = [], [], [], [], [] ##length 사용처 수정 필요
    mel_len_list = []
    
    for speech_temp, src_temp, tgt_temp in batch:
                        
        mel_len_list.append(speech_temp.shape[0]) ## speech_temp shape = length, 80
        
        src_speech.append(speech_temp) 
        
        tokend_src_text = text_transform['kr'](src_temp)
        tokend_tgt_text = text_transform['en'](tgt_temp)
                
        src_text.append(tokend_src_text)
        tgt_text.append(tokend_tgt_text)
        
        src_text_length.append(len(tokend_src_text)) ##text의 길이
        tgt_text_length.append(len(tokend_tgt_text))
    
    mel_len_max = max(mel_len_list)
    
    speech_batch = pad_sequence(src_speech, padding_value = 0.0, batch_first = True) # batch, length, dim
    src_batch = pad_sequence(src_text, padding_value = 0.0, batch_first = True)
    tgt_batch = pad_sequence(tgt_text, padding_value = 0.0, batch_first = True)  ## batch, sequence
            
    return speech_batch, src_batch, tgt_batch, torch.LongTensor(mel_len_list), torch.tensor(mel_len_max), torch.tensor(src_text_length), torch.tensor(tgt_text_length)

## speech, src_text, tgt_text, mel_lengths, max_mel_length_value, src_text_lengths, tgt_text_lengths

In [68]:
train_dataset = audio_dataset(example_data, 'train')
valid_dataset = audio_dataset(eval_data, 'dev')

train_loader = DataLoader(train_dataset, batch_size = 64, shuffle = True, collate_fn = collate_fn, drop_last = True,
                          num_workers = 15, pin_memory = True )

valid_loader = DataLoader(valid_dataset, batch_size = 64, shuffle = False, collate_fn = collate_fn, drop_last = True,
                         num_workers = 15, pin_memory = True)

In [24]:
def train(model, optimizer, train_loader, valid_loader = None):
    model.train()
    train_losses = 0
    val_losses = 0
    total_ASR_CE_loss = 0
    total_ASR_CTC_loss= 0
    total_MT_loss = 0
    total_MT_CTC_loss = 0
    accumulation_steps = 2
    
    
    for i, (speech, src_text, tgt_text, mel_len_list, mel_len_max, src_text_length, tgt_text_length) in tqdm(enumerate(train_loader)):
        '''
        src : batch,lengh, dim
        tgt : batch seq
        '''
        
        src_speech = speech.to(device) ## batch, length, dim
        
        src_text = src_text.to(device) ## batch, seq
        tgt_text = tgt_text.to(device) ## batch, seq
                
        mel_len_list = mel_len_list.to(device)
        
        ASR_tgt_input = src_text[:, :-1]    ## 입력은 더미 데이터 까지 포함하여서  
        ASR_tgt_output = src_text[:, 1:] #tgt[1:-1, 1:]  [1:-1] >> 더미 데이터는 제거한 나머지 특징값, [1:] >> sos 이후의 글자들
        
        ASR_tgt_mask, ASR_tgt_padding_mask = create_mask(ASR_tgt_input)
        ASR_tgt_mask = ASR_tgt_mask.to(device)
        ASR_tgt_padding_mask = ASR_tgt_padding_mask.to(device) 
        
        MT_tgt_input = tgt_text[:, :-1]
        MT_tgt_output = tgt_text[:, 1:]
        
        MT_tgt_mask, MT_tgt_padding_mask = create_mask(MT_tgt_input)
        MT_tgt_mask = MT_tgt_mask.to(device)
        MT_tgt_padding_mask = MT_tgt_padding_mask.to(device) 
        
        optimizer.zero_grad()
        
        ASR_logits, ASR_ctc_logits, MT_logits, MT_ctc_logits = model(src_speech, ASR_tgt_input, ASR_tgt_mask, ASR_tgt_padding_mask,
                                                      MT_tgt_input, MT_tgt_mask, MT_tgt_padding_mask, mel_len_list)

        
        ASR_loss = loss_fn(ASR_logits.reshape(-1, ASR_logits.shape[-1]), ASR_tgt_output.reshape(-1)) ##logit.reshape >> [batch * seq, dim], ## tgt_output [batch * seq]
                
        input_length = torch.full(size=(ASR_ctc_logits.size(0),), fill_value=ASR_ctc_logits.size(1), dtype=torch.long)
        
        ASR_loss2 = loss_fn2(ASR_ctc_logits.permute(1,0,2).log_softmax(2), ASR_tgt_output, input_length, src_text_length -1)

        
        MT_loss = loss_fn(MT_logits.reshape(-1, MT_logits.shape[-1]), MT_tgt_output.reshape(-1))
        
        MT_input_length = torch.full(size=(MT_ctc_logits.size(0),), fill_value=MT_ctc_logits.size(1), dtype=torch.long)
        
        MT_loss2 = loss_fn2(MT_ctc_logits.permute(1,0,2).log_softmax(2), MT_tgt_output, MT_input_length, tgt_text_length -1)
        
        total_loss = (0.7 * ASR_loss) + (0.3 * ASR_loss2) + (0.7 * MT_loss) + (0.3 * MT_loss2) 
        
        ASR_CE_loss = (0.7 * ASR_loss)
        ASR_CTC_loss= (0.3 * ASR_loss2)
        
        MT_CE_loss = (0.7 * MT_loss)
        MT_CTC_loss = (0.3 * MT_loss2)
        
        total_loss.backward()
  
        optimizer.step()
        
        #loss.backward()
                
        #optimizer.step()
        
        train_losses += total_loss.item()
        
        total_ASR_CE_loss += ASR_CE_loss
        total_ASR_CTC_loss += ASR_CTC_loss
        total_MT_loss += MT_CE_loss
        total_MT_CTC_loss += MT_CTC_loss
    
    print(f"total_ASR_CE = {(total_ASR_CE_loss / len(train_loader)):.4f}, total_ASR_CTC_loss = {(total_ASR_CTC_loss/len(train_loader)):.4f},\
    total_MT_CE_loss = {(total_MT_loss / len(train_loader)):.4f}, total_MT_CTC_loss = {(total_MT_CTC_loss / len(train_loader)):.4f}")
    
    train_losses /= len(train_loader)
    
    total_ASR_CE_loss = 0
    total_ASR_CTC_loss= 0
    total_MT_loss = 0
    total_MT_CTC_loss = 0
    
        
    for speech, src_text, tgt_text, mel_len_list, mel_len_max, src_text_length, tgt_text_length in tqdm(valid_loader):
        model.eval()
        with torch.no_grad():

            src_speech = speech.to(device) ## batch, length, dim

            src_text = src_text.to(device) ## batch, seq
            tgt_text = tgt_text.to(device) ## batch, seq

            mel_len_list = mel_len_list.to(device)

            ASR_tgt_input = src_text[:, :-1]    ## 입력은 더미 데이터 까지 포함하여서  
            ASR_tgt_output = src_text[:, 1:] #tgt[1:-1, 1:]  [1:-1] >> 더미 데이터는 제거한 나머지 특징값, [1:] >> sos 이후의 글자들

            ASR_tgt_mask, ASR_tgt_padding_mask = create_mask(ASR_tgt_input)
            ASR_tgt_mask = ASR_tgt_mask.to(device)
            ASR_tgt_padding_mask = ASR_tgt_padding_mask.to(device) 

            MT_tgt_input = tgt_text[:, :-1]
            MT_tgt_output = tgt_text[:, 1:]

            MT_tgt_mask, MT_tgt_padding_mask = create_mask(MT_tgt_input)
            MT_tgt_mask = MT_tgt_mask.to(device)
            MT_tgt_padding_mask = MT_tgt_padding_mask.to(device)
            
            ASR_logits, ASR_ctc_logits, MT_logits, MT_ctc_logits = model(src_speech, ASR_tgt_input, ASR_tgt_mask, ASR_tgt_padding_mask,
                                                      MT_tgt_input, MT_tgt_mask, MT_tgt_padding_mask, mel_len_list)
            
            ASR_loss = loss_fn(ASR_logits.reshape(-1, ASR_logits.shape[-1]), ASR_tgt_output.reshape(-1)) ##logit.reshape >> [batch * seq, dim], ## tgt_output [batch * seq]

            MT_loss = loss_fn(MT_logits.reshape(-1, MT_logits.shape[-1]), MT_tgt_output.reshape(-1))

            total_loss = ASR_loss + MT_loss
            
            val_losses += total_loss.item() ## item.detach            
            total_ASR_CE_loss += ASR_loss.item()
            total_MT_loss += MT_loss.item()

    print(f"VALID = total_ASR_CE = {(total_ASR_CE_loss / len(valid_loader)):.4f}, total_MT_loss = {(total_MT_loss / len(valid_loader)):.4f}")
    
    val_losses /= len(valid_loader)
    
    return train_losses, val_losses

In [25]:
before_val_loss = 9999.0
patient = 0

t = open('cvss_conformer_train_loss_ST_Branch','w')
v = open('cvss_conformer_valid_loss_ST_Branch','w')


for epoch in range(0, 10000):
    
    t = open('cvss_conformer_train_loss_ST_Branch','a')
    v = open('cvss_conformer_valid_loss_ST_Branch','a')   
    
    try:
        start_time = timer()
        train_loss, valid_loss = train(transformer, optimizer, train_loader, valid_loader)
        end_time = timer()
        #scheduler.step()
    
        print(f"Epoch = {epoch}, Train_loss ={train_loss:.4f}, Valid_loss= {valid_loss:.4f}")
        t.write(str(train_loss) + '\n')
        v.write(str(valid_loss) + '\n')
        
    finally:
        t.close()
        v.close()
    
    if valid_loss < before_val_loss:
        print('!!!model_saved!!!')
        torch.save(transformer.state_dict(), './cvss_model_save/cvss_conformer_ST_Branch.pt')
        before_val_loss = valid_loss
#         patient = 0
    
#     else:
#         patient += 1
#         if patient == 30:
#             print("overfitting")
#             break
            


2040it [09:42,  3.50it/s]


total_ASR_CE = 4.1742, total_ASR_CTC_loss = 2.2926,    total_MT_CE_loss = 4.2708, total_MT_CTC_loss = 2.3318


100%|█████████████████████████████████████████| 230/230 [00:53<00:00,  4.28it/s]


VALID = total_ASR_CE = 5.4134, total_MT_loss = 5.6680
Epoch = 0, Train_loss =13.0695, Valid_loss= 11.0814
!!!model_saved!!!


2040it [09:42,  3.50it/s]


...

VALID = total_ASR_CE = 1.8242, total_MT_loss = 2.9243
Epoch = 351, Train_loss =5.1978, Valid_loss= 4.7485



2040it [10:12,  3.33it/s]


total_ASR_CE = 1.5244, total_ASR_CTC_loss = 0.5907,    total_MT_CE_loss = 2.1009, total_MT_CTC_loss = 0.9698


 46%|██████████████████▋                      | 105/230 [00:27<00:32,  3.88it/s]


KeyboardInterrupt: 

In [69]:
def translate_bleu(model,testset, vocab):
    total_bleu = 0
    total_wer = 0
    total_cer = 0
    acc = 0
    model.eval()
    with torch.no_grad():
        for loader_idx ,(src_speech, src_text, tgt_text, lengths, _, src_text_length, tgt_text_length) in tqdm(enumerate(testset)):
            ''' 
            src (speech, Tensor): batch, seq, dim
            tgt (text, Tensor): batch, seq, 
            '''
            
            src_speech = src_speech.to(device)
            src_text = src_text.to(device)
            tgt_text = tgt_text.to(device)
            
            
            lengths = lengths.to(device)
            
            #src_text_length = src_text.size(1)
            src_text_max_len = src_text_length.max().tolist()
                         
            ASR_tgt_tokens = ASR_greedy_decode(model, lengths, src_text_max_len, src_speech, start_symbol=2) ## (batch, length)  #.flatten()
            ASR_tgt_tokens = ASR_tgt_tokens.to(device)            
       
            decoded_words = [] ## 예측 문장들을 담는 list ## 예측 결과
            real_sentences = []
            
            
            for batch_idx in range(src_text.size(0)):                       ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                
                batch_subwords = ASR_tgt_tokens[batch_idx].tolist()             ## idx 번째 배치의 문장 가져오기, batch_subwords
                
                real_text = src_text[batch_idx].tolist()
                                
                
                if 3 not in batch_subwords:
                    print(f"not in eos token : {batch_subwords}")
                    print(vocab.DecodeIds(batch_subwords))
                    decoded_words.append(vocab.IdToPiece(batch_subwords))
        
                else:
                    eos_index = batch_subwords.index(3)                            ## eos 토큰을 나타내는  3 찾기 #'>>>>>>> 3 없을 시 예외처리 필요
                    batch_subwords = batch_subwords[:eos_index + 1]    ##list
                    print(f"predicted_ {vocab.DecodeIds(batch_subwords)}")
                    decoded_words.append(vocab.IdToPiece(batch_subwords))
                
                real_eos_index = real_text.index(3)
                real_text = real_text[:real_eos_index+1]
                
                print(f"real_ {vocab.DecodeIds(real_text)}")
                real_sentences.append(vocab.IdToPiece(real_text))
                
                print("-------------------------------------------")
                
                bleu = sentence_bleu([real_sentences[batch_idx]], decoded_words[batch_idx], smoothing_function =None )
                
                total_bleu += bleu
                    
            wer = word_error_rate(preds= vocab.DecodeIds(decoded_words), target = vocab.DecodeIds(real_sentences)).item()
            cer = char_error_rate(preds= vocab.DecodeIds(decoded_words), target = vocab.DecodeIds(real_sentences)).item()
            total_wer += wer
            total_cer += cer

        
    return total_bleu / len(testset.dataset), total_wer/ len(testset), total_cer/ len(testset)

In [70]:
def ASR_greedy_decode(model, lengths, src_target_max_len, src_speech, start_symbol = 2):
    
    lengths = torch.tensor(list(map(int , (lengths / 4)))).to(device)
    ASR_memory = model.encode(src_speech, lengths) ## Batch, Sequence, feature
    ASR_encoder_padding_mask = ASR_memory[2]
    ASR_memory = ASR_memory[0]
    
    ys_ASR = torch.ones(src_speech.size(0),1).fill_(start_symbol).type(torch.long).to(device) # 배치 크기만큼 시작 토큰 생성 ## 처음 시작은 <sos> 토큰 ## batch, seq
    
    ys_MT = torch.ones(src_speech.size(0),1).fill_(start_symbol).type(torch.long).to(device)
    
    for i in range(src_target_max_len): ## 최대 시퀀스 length 만큼 반복
        
        ASR_tgt_mask = (generate_square_subsequent_mask(ys_ASR.size(1))).to(device) ## 시퀀스 길이 만큼의 마스킹 길이
        
        MT_tgt_mask = (generate_square_subsequent_mask(ys_MT.size(1))).to(device)
        
        out, _ = model.decoder(ys_ASR, ASR_memory, ASR_tgt_mask, ASR_encoder_padding_mask, ys_MT, MT_tgt_mask) ## out = batch,sequence, hidden
        
        prob = model.src_generator(out[:, -1]) ## output[:, -1] >>  각 배치의 시퀀스에서 마지막 단어
        _, next_word = torch.max(prob, dim = 1)
        next_word = next_word.unsqueeze(1)
        ys_ASR = torch.cat([ys_ASR, next_word], dim = 1) ## >> batch,length
        
    return ys_ASR

In [71]:
def translate_bleu_MT(model,testset, vocab):
    total_bleu = 0
    total_wer = 0
    total_cer = 0
    acc = 0
    model.eval()
    with torch.no_grad():
        for loader_idx ,(src_speech, src_text, tgt_text, lengths, _, src_text_length, tgt_text_length) in tqdm(enumerate(testset)):
            ''' 
            src (speech, Tensor): batch, seq, dim
            tgt (text, Tensor): batch, seq, 
            '''
            
            src_speech = src_speech.to(device)
            src_text = src_text.to(device)
            tgt_text = tgt_text.to(device)
            
            
            lengths = lengths.to(device)
            
            #src_text_length = src_text.size(1)
            tgt_text_length = tgt_text_length.max().tolist()
            
            
            ASR_tgt_tokens = MT_greedy_decode(model, lengths, tgt_text_length, src_speech, start_symbol=2) ## (batch, length)  #.flatten()
            ASR_tgt_tokens = ASR_tgt_tokens.to(device)            
       
            decoded_words = [] ## 예측 문장들을 담는 list ## 예측 결과
            real_sentences = []
            
            
            for batch_idx in range(tgt_text.size(0)):                       ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                
                batch_subwords = ASR_tgt_tokens[batch_idx].tolist()             ## idx 번째 배치의 문장 가져오기, batch_subwords
                
                real_text = tgt_text[batch_idx].tolist()
                                
                
                if 3 not in batch_subwords:
                    print(f"not in eos token : {batch_subwords}")
                    print(vocab.DecodeIds(batch_subwords))
                    decoded_words.append(vocab.IdToPiece(batch_subwords))
        
                else:
                    eos_index = batch_subwords.index(3)                            ## eos 토큰을 나타내는  3 찾기 #'>>>>>>> 3 없을 시 예외처리 필요
                    batch_subwords = batch_subwords[:eos_index + 1]    ##list
                    print(f"predicted_ {vocab.DecodeIds(batch_subwords)}")
                    decoded_words.append(vocab.IdToPiece(batch_subwords))
                
                #real_text = tgt_text[batch_idx].tolist()
                real_eos_index = real_text.index(3)
                real_text = real_text[:real_eos_index+1]
                
                print(f"real_ {vocab.DecodeIds(real_text)}")
                real_sentences.append(vocab.IdToPiece(real_text))
                
                print("-------------------------------------------")
                
                bleu = sentence_bleu([real_sentences[batch_idx]], decoded_words[batch_idx], smoothing_function =None )
                
                total_bleu += bleu
                    
            wer = word_error_rate(preds= vocab.DecodeIds(decoded_words), target = vocab.DecodeIds(real_sentences)).item()
            cer = char_error_rate(preds= vocab.DecodeIds(decoded_words), target = vocab.DecodeIds(real_sentences)).item()
            total_wer += wer
            total_cer += cer

        
    return total_bleu / len(testset.dataset), total_wer/ len(testset), total_cer/ len(testset)

In [72]:
def MT_greedy_decode(model, lengths, src_target_max_len, src_speech, start_symbol = 2):
    
    lengths = torch.tensor(list(map(int , (lengths / 4)))).to(device)
    ASR_memory= model.encode(src_speech, lengths) ## Batch, Sequence, feature
    ASR_encoder_padding_mask = ASR_memory[2]
    ASR_memory = ASR_memory[0]
    
    
    ys_ASR = torch.ones(src_speech.size(0),1).fill_(start_symbol).type(torch.long).to(device) # 배치 크기만큼 시작 토큰 생성 ## 처음 시작은 <sos> 토큰 ## batch, seq
    
    ys_MT = torch.ones(src_speech.size(0),1).fill_(start_symbol).type(torch.long).to(device)
    
    for i in range(src_target_max_len): ## 최대 시퀀스 length 만큼 반복
        
        ASR_tgt_mask = (generate_square_subsequent_mask(ys_ASR.size(1))).to(device) ## 시퀀스 길이 만큼의 마스킹 길이
        
        MT_tgt_mask = (generate_square_subsequent_mask(ys_MT.size(1))).to(device)
        
        
        _, out = model.decoder(ys_ASR, ASR_memory, ASR_tgt_mask, ASR_encoder_padding_mask, ys_MT, MT_tgt_mask) ## out = batch,sequence, hidden
        
        prob = model.tgt_generator(out[:, -1]) ## output[:, -1] >>  각 배치의 시퀀스에서 마지막 단어
        _, next_word = torch.max(prob, dim = 1)
        next_word = next_word.unsqueeze(1)
        ys_MT = torch.cat([ys_MT, next_word], dim = 1) ## >> batch,length
        
    return ys_MT

In [73]:
transformer.load_state_dict(torch.load("../weights/cvss_conformer_ST_multi-decoder.pt", map_location={"cuda:0":f"cuda:{0}"})) ## gpu 0번째에 할당




<All keys matched successfully>

In [76]:
bleu, wer, cer = translate_bleu(transformer, valid_loader, kr_vocab)
print(bleu, wer, cer)

1it [00:03,  3.35s/it]

predicted_ elle va permettre de favoriser durablement une fille riche en emplois non délocalisables.
real_ elle va permettre de favoriser durablement une filière riche en emplois non délocalisables.
-------------------------------------------
predicted_ il faut réhabiliter l’impôt la contribution à la charge commune.
real_ il faut réhabiliter l’impôt la contribution à la charge commune.
-------------------------------------------
predicted_ je retire l’amendement numéro cinq cent cinquante-cinq.
real_ je retire l’amendement numéro cent cinquante-cinq.
-------------------------------------------
predicted_ or jean-patrick gill vient de dire que la tante était très forte.
real_ or jean-patrick gille vient de dire que l’attente était très forte.
-------------------------------------------
predicted_ je mets aux voix l’amendement numéro un.
real_ je mets aux voix l’amendement numéro un.
-------------------------------------------
predicted_ la parole est à monsieur françois poupony pour le

2it [00:04,  1.78s/it]

predicted_ le problème que vous soulevez s’oppose.
real_ le problème que vous soulevez se pose.
-------------------------------------------
predicted_ il convient en effet de supprimer l’article premier a b qui introduit un doublelon.
real_ il convient en effet de supprimer l’article premier ab qui introduit un doublon.
-------------------------------------------
predicted_ la france est un grand pays nous en sommes convaincus.
real_ la france est un grand pays nous en sommes convaincus.
-------------------------------------------
predicted_ monsieur paul a raison il faut que cela sert d’exemple.
real_ monsieur paul a raison il faut que cela serve d’exemple.
-------------------------------------------
predicted_ voilà ce qui nous différencie.
real_ voilà ce qui nous différencie.
-------------------------------------------
predicted_ porte est limitée donc mais  ⁇ util c’est très important.
real_ portée limitée donc mais utile c’est très important.
--------------------------------------

3it [00:04,  1.30s/it]

...

predicted_ on voit que dans le siècle dernier on vivait beaucoup au cours du feu.
real_ on voit que dans le siècle dernier on vivait beaucoup au coin du feu.
-------------------------------------------
predicted_ la grande majorité des pseudogènes ne montre pas de signe d'activité.
real_ la grande majorité des pseudogènes ne montrent pas de signe d'activité.
-------------------------------------------
predicted_ les réalisations en réalité augmentées font partie de l'art remercie.
real_ les réalisations en réalité augmentée font partie de l'art immersif.
-------------------------------------------
predicted_ l'architecte initial avait été joseph ferdinand picher.
real_ l'architecte initial avait été joseph-ferdinand peachy.
-------------------------------------------
predicted_ luca alcaras lui succède.
real_ lucas alcaraz lui succède.
-------------------------------------------
predicted_ c’est la situation la plus favorable.
real_ c'est la situation la plus favorable.
---------------

230it [02:36,  1.55it/s]

predicted_ les chansons du duo sont un mélange de français d'espagnol et d'anglais.
real_ les chansons du duo sont un mélange de français d'espagnol et d'anglais.
-------------------------------------------
predicted_ valaine plan humanise les objets et les animaux et l’anomalise les humains.
real_ valle-inclán humanise les objets et les animaux et il animalise les humains.
-------------------------------------------
predicted_ elle gagne le titre de miss congénitalité durant la finale de la saison.
real_ elle gagne le titre de miss congeniality durant la finale de la saison.
-------------------------------------------
predicted_ lionel a la malchance d'être victime deux reprises de cruel flagilation.
real_ lionel a la malchance d'être victime à deux reprises de cruelles flagellations.
-------------------------------------------
predicted_ les soldats australiens fegiens jamaïcains malés néo-zélandais et singaporiens utilisaient des d'australie.
real_ les soldats australiens fidjiens j

230it [02:37,  1.46it/s]

0.6717158738856995 0.20618521661862083 0.07663018546350624


In [75]:
bleu, wer, cer = translate_bleu_MT(transformer, valid_loader, en_vocab)
print(bleu, wer, cer)


1it [00:03,  3.14s/it]

predicted_ she will allow for durably favor a rich girl in non delocalized jobs.
real_ it'll help spur the growth of that sector continuously which counts many jobs that cannot be relocated.
-------------------------------------------
predicted_ the contributions must be rehabilitated the commune charge.
real_ it is necessary to rehabilitate the tax the contribution to the common charge.
-------------------------------------------
predicted_ i withdraw amendment number five hundred fifty five.
real_ i withdraw amendment number one hundred and fifty five.
-------------------------------------------
predicted_ yet jean patrick gill comes to say the aunt was very strong.
real_ but jean patrick gille just said that the wait is not that long.
-------------------------------------------
predicted_ i'm putting amendment number one to the vote.
real_ i will now put to the vote amendment number one.
-------------------------------------------
predicted_ the floor is open to mr francois pponi to

2it [00:03,  1.64s/it]

predicted_ the problem you lifted is opposed.
real_ the problem that you are bringing up is arising.
-------------------------------------------
predicted_ it indeed delete article a b that introduces a double.
real_ we can in fact agree to delete the primary clause a b which introduces a duplicate.
-------------------------------------------
predicted_ france is a great country we are convinced of it.
real_ france is a big country we are convinced about it.
-------------------------------------------
predicted_ mr paul is right it must be used for example.
real_ mr paul was right it must be used as an example.
-------------------------------------------
predicted_ that's what differentiates us.
real_ that what makes us different.
-------------------------------------------
predicted_ so limited door is very important.
real_ limited scope them but useful it's very important.
-------------------------------------------
predicted_ the floor is now open to mr marc fesnaud to support the f

3it [00:04,  1.21s/it]

...

predicted_ we can see that in the last century we lived a lot during the fire.
real_ we see that in the last century people spent more time near the fireplace.
-------------------------------------------
predicted_ the great majority of pseudogenic fires no activity sign.
real_ the vast majority of the pseudogenes don't show any sign of activity.
-------------------------------------------
predicted_ the realizations in reality are part of the mercive art.
real_ the achievements in enhanced reality are part of immersive arts.
-------------------------------------------
predicted_ the initial architect had been jose ferdinand piché.
real_ the initial architect was joseph ferdinand peachy.
-------------------------------------------
predicted_ luca al carras succeeded him.
real_ lucas alcaraz succeeds him.
-------------------------------------------
predicted_ it is the most favorable situation.
real_ it is the best situation.
-------------------------------------------
predicted_ it is 

230it [02:33,  1.58it/s]

predicted_ the songs of the duo are a mix of french spanish and english.
real_ the songs of the duo are a mix of french spanish and english.
-------------------------------------------
predicted_ vallen plan humaniz the objects and animals and analize the human ones.
real_ valle inclan humanizes objects and animals and animates humans.
-------------------------------------------
predicted_ she won the title of miss kangenality during the final of the season.
real_ she won the title o d miss congeniality during the season finale.
-------------------------------------------
predicted_ lionel has the luck to be victim twice during cluel flagilation.
real_ lionel has the misfortune of being victim twice of a cruel flogging.
-------------------------------------------
not in eos token : [2, 7, 4572, 5646, 19, 2670, 202, 112, 2106, 3817, 1332, 882, 163, 136, 51, 96, 46, 869, 169, 232, 343, 531, 4810, 1663, 157]
the australian soldier fijian jamaican malais neoseland and singaporeans used wea

230it [02:33,  1.49it/s]

0.2754061452539678 0.5592725749896921 0.38668061287506766
